In [1]:
# 0. Setup: GPU, installs, imports
# ============================================================
!nvidia-smi

!pip install -q ptflops

import os
import glob
import math
import time

from PIL import Image
import numpy as np

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader

import torchvision.transforms as T
import torchvision.transforms.functional as TF

from ptflops import get_model_complexity_info

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print("Device:", device)


Mon Nov 24 04:19:02 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 560.35.03              Driver Version: 560.35.03      CUDA Version: 12.6     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA H100 NVL                Off |   00000000:C3:00.0 Off |                    0 |
| N/A   33C    P0             60W /  350W |       1MiB /  95830MiB |      0%      Default |
|                                         |                        |             Disabled |
+-----------------------------------------+-----

In [3]:
#from google.colab import drive
#drive.mount('/content/drive')

import os
BASE_DIR = "/home/017510844/projects/anshu"
os.makedirs(BASE_DIR, exist_ok=True)

# Optional: clean old extracted folders to avoid any conflicts
#!rm -rf "{BASE_DIR}/HR_train" "{BASE_DIR}/LR_train" "{BASE_DIR}/HR_val" "{BASE_DIR}/LR_val"

# Unzip from Drive → /content/data/... and overwrite if exists (-o)
#!unzip -oq "/content/drive/MyDrive/HR_train.zip" -d "{BASE_DIR}/HR_train"
#!unzip -oq "/content/drive/MyDrive/LR_train.zip" -d "{BASE_DIR}/LR_train"
#!unzip -oq "/content/drive/MyDrive/HR_val.zip"   -d "{BASE_DIR}/HR_val"
#!unzip -oq "/content/drive/MyDrive/LR_val.zip"   -d "{BASE_DIR}/LR_val"

HR_TRAIN_DIR = os.path.join(BASE_DIR, "/home/017510844/projects/anshu/HR_train")
LR_TRAIN_DIR = os.path.join(BASE_DIR, "/home/017510844/projects/anshu/LR_train")
HR_VAL_DIR   = os.path.join(BASE_DIR, "/home/017510844/projects/anshu/HR_val")
LR_VAL_DIR   = os.path.join(BASE_DIR, "/home/017510844/projects/anshu/LR_val")

print("HR_TRAIN_DIR:", HR_TRAIN_DIR)
print("LR_TRAIN_DIR:", LR_TRAIN_DIR)
print("HR_VAL_DIR:", HR_VAL_DIR)
print("LR_VAL_DIR:", LR_VAL_DIR)


HR_TRAIN_DIR: /home/017510844/projects/anshu/HR_train
LR_TRAIN_DIR: /home/017510844/projects/anshu/LR_train
HR_VAL_DIR: /home/017510844/projects/anshu/HR_val
LR_VAL_DIR: /home/017510844/projects/anshu/LR_val


In [4]:
!ls -R /content/data/HR_train
!ls -R /content/data/LR_train
!ls -R /content/data/HR_val
!ls -R /content/data/LR_val


ls: cannot access '/content/data/HR_train': No such file or directory
ls: cannot access '/content/data/LR_train': No such file or directory
ls: cannot access '/content/data/HR_val': No such file or directory
ls: cannot access '/content/data/LR_val': No such file or directory


In [5]:
# Point to the *actual* image folders
HR_TRAIN_DIR = "/home/017510844/projects/anshu/HR_train/train"
LR_TRAIN_DIR = "/home/017510844/projects/anshu/LR_train/train"
HR_VAL_DIR   = "/home/017510844/projects/anshu/HR_val/val"
LR_VAL_DIR   = "/home/017510844/projects/anshu/LR_val/val"

print("HR_TRAIN_DIR:", HR_TRAIN_DIR)
print("LR_TRAIN_DIR:", LR_TRAIN_DIR)
print("HR_VAL_DIR  :", HR_VAL_DIR)
print("LR_VAL_DIR  :", LR_VAL_DIR)

HR_TRAIN_DIR: /home/017510844/projects/anshu/HR_train/train
LR_TRAIN_DIR: /home/017510844/projects/anshu/LR_train/train
HR_VAL_DIR  : /home/017510844/projects/anshu/HR_val/val
LR_VAL_DIR  : /home/017510844/projects/anshu/LR_val/val


In [6]:
import os
import random
from PIL import Image

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
import torchvision.transforms as T
import torchvision.transforms.functional as TF

# ============================================================
# 0. Config / paths  (make sure these are correct)
# ============================================================
IMG_SIZE   = 256
IMG_EXTS   = (".png", ".jpg", ".jpeg", ".bmp")
BATCH_SIZE = 8


to_tensor = T.ToTensor()
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [7]:
# ============================================================
# 1. Dataset + Dataloaders
# ============================================================
class SuperResolutionDataset(Dataset):
    def __init__(self, lr_dir, hr_dir, train=True):
        self.lr_dir = lr_dir
        self.hr_dir = hr_dir
        self.train  = train

        self.files = sorted(
            f for f in os.listdir(hr_dir)
            if f.lower().endswith(IMG_EXTS)
        )

    def __len__(self):
        return len(self.files)

    def __getitem__(self, idx):
        fname   = self.files[idx]
        hr_path = os.path.join(self.hr_dir, fname)
        lr_path = os.path.join(self.lr_dir, fname)

        hr_img = Image.open(hr_path).convert("RGB")
        lr_img = Image.open(lr_path).convert("RGB")

        hr = to_tensor(hr_img)              # [3, 256, 256]
        lr = to_tensor(lr_img)              # [3, 256, 256]

        # keep size same but smooth LR a bit
        lr_up = TF.resize(lr, (IMG_SIZE, IMG_SIZE), interpolation=Image.BICUBIC)

        if self.train and random.random() < 0.5:
            lr_up = TF.hflip(lr_up)
            hr    = TF.hflip(hr)

        return lr_up, hr

train_dataset = SuperResolutionDataset(LR_TRAIN_DIR, HR_TRAIN_DIR, train=True)
val_dataset   = SuperResolutionDataset(LR_VAL_DIR,   HR_VAL_DIR,   train=False)

print("Train size:", len(train_dataset))
print("Val size  :", len(val_dataset))

train_loader = DataLoader(
    train_dataset,
    batch_size=BATCH_SIZE,
    shuffle=True,
    num_workers=0,      # <= changed from 2
    pin_memory=True,
)

val_loader = DataLoader(
    val_dataset,
    batch_size=BATCH_SIZE,
    shuffle=False,
    num_workers=0,      # <= changed from 2
    pin_memory=True,
)


Train size: 258
Val size  : 100


In [8]:
# ============================================================
# 2. EDSR-Mini model (deeper-but-narrower: 48 feats, 12 blocks)
# ============================================================
import torch
import torch.nn as nn
from torch import amp

# ---- Residual Block for EDSR ----
class ResidualBlockEDSR(nn.Module):
    def __init__(self, n_feat: int, res_scale: float = 0.1):
        super().__init__()
        self.body = nn.Sequential(
            nn.Conv2d(n_feat, n_feat, 3, 1, 1),
            nn.ReLU(inplace=True),
            nn.Conv2d(n_feat, n_feat, 3, 1, 1),
        )
        self.res_scale = res_scale

    def forward(self, x):
        res = self.body(x) * self.res_scale
        return x + res


# ---- EDSR-Mini network (same-size SR) ----
class EDSRMini(nn.Module):
    """
    Lightweight EDSR-style network for same-size SR:
    - Input : [B, 3, H, W] (bicubic-upsampled LR)
    - Output: [B, 3, H, W] (sharpened SR)
    """
    def __init__(self, in_ch=3, out_ch=3, n_feat=48, n_blocks=12, res_scale=0.1):
        super().__init__()

        self.head = nn.Conv2d(in_ch, n_feat, 3, 1, 1)

        body = []
        for _ in range(n_blocks):
            body.append(ResidualBlockEDSR(n_feat, res_scale=res_scale))
        # final conv in body
        body.append(nn.Conv2d(n_feat, n_feat, 3, 1, 1))
        self.body = nn.Sequential(*body)

        self.tail = nn.Conv2d(n_feat, out_ch, 3, 1, 1)

    def forward(self, x):
        x0 = self.head(x)
        res = self.body(x0)
        res = res + x0           # long skip
        out = self.tail(res)
        return out + x           # global residual (input already HR-sized)


# ---- Weight init ----
def init_weights(m):
    if isinstance(m, nn.Conv2d):
        nn.init.kaiming_normal_(m.weight, nonlinearity="relu")
        if m.bias is not None:
            nn.init.zeros_(m.bias)


# ---- Create model ----
N_FEAT   = 48
N_BLOCKS = 12

model = EDSRMini(
    in_ch=3,
    out_ch=3,
    n_feat=N_FEAT,
    n_blocks=N_BLOCKS,
    res_scale=0.1,
).to(device)

model.apply(init_weights)

print(model)
total_params = sum(p.numel() for p in model.parameters())
print("Total params (M):", total_params / 1e6)

# Complexity (GMac) – assumes get_model_complexity_info already imported
macs, params_str = get_model_complexity_info(
    model,
    (3, IMG_SIZE, IMG_SIZE),
    as_strings=True,
    print_per_layer_stat=False,
    verbose=False,
)
print("EDSR-Mini Params:", params_str)
print("EDSR-Mini MACs :", macs)



EDSRMini(
  (head): Conv2d(3, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (body): Sequential(
    (0): ResidualBlockEDSR(
      (body): Sequential(
        (0): Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
        (1): ReLU(inplace=True)
        (2): Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      )
    )
    (1): ResidualBlockEDSR(
      (body): Sequential(
        (0): Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
        (1): ReLU(inplace=True)
        (2): Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      )
    )
    (2): ResidualBlockEDSR(
      (body): Sequential(
        (0): Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
        (1): ReLU(inplace=True)
        (2): Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      )
    )
    (3): ResidualBlockEDSR(
      (body): Sequential(
        (0): Conv2d(48, 48, kernel_size=(3, 3), stride=(1, 1), pa

In [9]:
# ============================================================
# 3. Extra train loader WITHOUT augmentation (for PSNR eval)
# ============================================================
from torch.utils.data import DataLoader

train_eval_dataset = SuperResolutionDataset(
    LR_TRAIN_DIR,
    HR_TRAIN_DIR,
    train=False,   # disables random flip
)

train_eval_loader = DataLoader(
    train_eval_dataset,
    batch_size=BATCH_SIZE,
    shuffle=False,
    num_workers=0,
    pin_memory=True,
)

print("Train (no-aug) size:", len(train_eval_dataset))


# ============================================================
# 4. PSNR utility
# ============================================================
import math

def batch_psnr(sr, hr, max_val=1.0):
    # sr, hr in [0,1]
    mse = torch.mean((sr - hr) ** 2, dim=[1, 2, 3])
    mse = torch.clamp(mse, min=1e-10)
    psnr = 10 * torch.log10(max_val**2 / mse)
    return psnr.mean().item()

Train (no-aug) size: 258


In [14]:
# ============================================================
# 5. Training setup (L1 loss, PSNR-focused)
# ============================================================
from torch.optim import Adam
from torch.optim.lr_scheduler import MultiStepLR
from tqdm.auto import tqdm

criterion = nn.L1Loss()

optimizer = Adam(model.parameters(), lr=1e-4, betas=(0.9, 0.999))

NUM_EPOCHS = 800
scheduler = MultiStepLR(
    optimizer,
    milestones=[300, 500, 750],
    gamma=0.5,
)

use_amp = (device.type == "cuda")
scaler = amp.GradScaler("cuda") if use_amp else None

# --- NEW: track best epoch + its train loss and val PSNR
best_epoch = 0
best_train_loss = float("inf")
best_val_psnr = 0.0

best_path = "/home/017510844/projects/anshu/notebook_checkpoints/best_edsr_mini_48x12.pth"


# ============================================================
# 6. Train on train_loader (HR_train/LR_train), validate on val_loader
# ============================================================
for epoch in range(1, NUM_EPOCHS + 1):
    # ---------- Train ----------
    model.train()
    running_loss = 0.0

    pbar = tqdm(train_loader, desc=f"Epoch {epoch}/{NUM_EPOCHS} [train]", leave=False)
    for lr_up, hr in pbar:
        lr_up = lr_up.to(device)
        hr    = hr.to(device)

        optimizer.zero_grad(set_to_none=True)

        if use_amp:
            with amp.autocast("cuda"):
                sr = model(lr_up)
                loss = criterion(sr, hr)

            scaler.scale(loss).backward()
            scaler.step(optimizer)
            scaler.update()
        else:
            sr = model(lr_up)
            loss = criterion(sr, hr)
            loss.backward()
            optimizer.step()

        running_loss += loss.item() * lr_up.size(0)
        pbar.set_postfix(loss=loss.item())

    train_loss = running_loss / len(train_dataset)

    # ---------- Validate ----------
    model.eval()
    val_psnr = 0.0
    val_batches = 0

    with torch.no_grad():
        for lr_up, hr in val_loader:
            lr_up = lr_up.to(device)
            hr    = hr.to(device)

            sr = model(lr_up).clamp(0.0, 1.0)
            val_psnr += batch_psnr(sr, hr)
            val_batches += 1

    val_psnr /= max(1, val_batches)
    scheduler.step()

    print(f"Epoch {epoch:03d}: train_loss={train_loss:.4f} | val_PSNR={val_psnr:.3f} dB")

    # --- NEW: update "best" based on val_PSNR and save a richer checkpoint
    if val_psnr > best_val_psnr:
        best_val_psnr = val_psnr
        best_epoch = epoch
        best_train_loss = train_loss

        checkpoint = {
            "epoch": best_epoch,
            "val_psnr": best_val_psnr,
            "train_loss": best_train_loss,
            "model_state": model.state_dict(),
            "optimizer_state": optimizer.state_dict(),
            "scheduler_state": scheduler.state_dict(),
            "amp": {
                "use_amp": use_amp,
                "scaler_state": (scaler.state_dict() if use_amp else None),
            },
        }
        torch.save(checkpoint, best_path)
        print(f"New best VAL PSNR: {best_val_psnr:.3f} dB @ epoch {best_epoch} → saved to {best_path}")

# --- NEW: final summary message
summary_msg = (
    f"Training done. Best @ epoch {best_epoch}: "
    f"train_loss={best_train_loss:.4f} | val_PSNR={best_val_psnr:.3f} dB. "
    f"Checkpoint: {best_path}"
)



Epoch 001: train_loss=0.0520 | val_PSNR=22.755 dB
New best VAL PSNR: 22.755 dB @ epoch 1 → saved to /home/017510844/projects/anshu/notebook_checkpoints/best_edsr_mini_48x12.pth


Epoch 002: train_loss=0.0503 | val_PSNR=22.774 dB
New best VAL PSNR: 22.774 dB @ epoch 2 → saved to /home/017510844/projects/anshu/notebook_checkpoints/best_edsr_mini_48x12.pth


Epoch 003: train_loss=0.0502 | val_PSNR=22.792 dB
New best VAL PSNR: 22.792 dB @ epoch 3 → saved to /home/017510844/projects/anshu/notebook_checkpoints/best_edsr_mini_48x12.pth


Epoch 004: train_loss=0.0501 | val_PSNR=22.844 dB
New best VAL PSNR: 22.844 dB @ epoch 4 → saved to /home/017510844/projects/anshu/notebook_checkpoints/best_edsr_mini_48x12.pth


Epoch 005: train_loss=0.0501 | val_PSNR=22.871 dB
New best VAL PSNR: 22.871 dB @ epoch 5 → saved to /home/017510844/projects/anshu/notebook_checkpoints/best_edsr_mini_48x12.pth


...

Epoch 796: train_loss=0.0470 | val_PSNR=23.155 dB


Epoch 797: train_loss=0.0471 | val_PSNR=23.155 dB


Epoch 798: train_loss=0.0470 | val_PSNR=23.144 dB


Epoch 799: train_loss=0.0471 | val_PSNR=23.153 dB


Epoch 800: train_loss=0.0471 | val_PSNR=23.141 dB


In [15]:
# --- NEW: final summary print
print(summary_msg)

Training done. Best @ epoch 785: train_loss=0.0471 | val_PSNR=23.159 dB. Checkpoint: /home/017510844/projects/anshu/notebook_checkpoints/best_edsr_mini_48x12.pth


In [12]:
!pip install -q onnx onnxscript

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.2/18.2 MB 131.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 683.0/683.0 kB 53.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.3/129.3 kB 12.8 MB/s eta 0:00:00


In [ ]:
import os
import logging
import torch

# -------------------------------------------------
# 0. Quiet down ONNX / torch.onnx logging
# -------------------------------------------------
logging.getLogger("torch.onnx").setLevel(logging.ERROR)
logging.getLogger("onnxscript").setLevel(logging.ERROR)

# 1. Model definition

class ResidualBlockEDSR(torch.nn.Module):
    def __init__(self, n_feat: int, res_scale: float = 0.1):
        super().__init__()
        self.body = torch.nn.Sequential(
            torch.nn.Conv2d(n_feat, n_feat, 3, 1, 1),
            torch.nn.ReLU(inplace=True),
            torch.nn.Conv2d(n_feat, n_feat, 3, 1, 1),
        )
        self.res_scale = res_scale

    def forward(self, x):
        res = self.body(x) * self.res_scale
        return x + res


class EDSRMini(torch.nn.Module):
    def __init__(self, in_ch=3, out_ch=3, n_feat=48, n_blocks=12, res_scale=0.1):
        super().__init__()
        self.head = torch.nn.Conv2d(in_ch, n_feat, 3, 1, 1)
        body = []
        for _ in range(n_blocks):
            body.append(ResidualBlockEDSR(n_feat, res_scale=res_scale))
        body.append(torch.nn.Conv2d(n_feat, n_feat, 3, 1, 1))
        self.body = torch.nn.Sequential(*body)
        self.tail = torch.nn.Conv2d(n_feat, out_ch, 3, 1, 1)

    def forward(self, x):
        x0 = self.head(x)
        res = self.body(x0)
        res = res + x0
        out = self.tail(res)
        return out + x

# -------------------------------------------------
# 2. Load best weights on CPU
# -------------------------------------------------
best_path = "/home/017510844/projects/anshu/notebook_checkpoints/best_edsr_mini_48x12.pth"
IMG_SIZE  = 256

model_onnx = EDSRMini(in_ch=3, out_ch=3, n_feat=48, n_blocks=12, res_scale=0.1)
model_onnx.load_state_dict(torch.load(best_path, map_location="cpu"))
model_onnx.eval()  # important for export

# Fixed-shape dummy input for 1x3x256x256
dummy_input = torch.randn(1, 3, IMG_SIZE, IMG_SIZE)

# -------------------------------------------------
# 3. Export to ONNX (opset 18, no conversion)
# -------------------------------------------------
os.makedirs("/home/017510844/projects/anshu", exist_ok=True)
onnx_path = "/home/017510844/projects/anshu/edsr_mini_48x12_static.onnx"

torch.onnx.export(
    model_onnx,
    dummy_input,
    onnx_path,
    export_params=True,
    opset_version=18,        # <- use 18 directly, no downgrade, no warning
    do_constant_folding=True,
    input_names=["input"],
    output_names=["output"],
    # no dynamic_axes -> static 1x3x256x256, good for NPU
)

print("ONNX saved to:", onnx_path)


[torch.onnx] Obtain model graph for `EDSRMini([...]` with `torch.export.export(..., strict=False)`...
[torch.onnx] Obtain model graph for `EDSRMini([...]` with `torch.export.export(..., strict=False)`... ✅
[torch.onnx] Run decomposition...
[torch.onnx] Run decomposition... ✅
[torch.onnx] Translate the graph into ONNX...
[torch.onnx] Translate the graph into ONNX... ✅
ONNX saved to: /content/onnx_out/edsr_mini_48x12_static.onnx


In [23]:
import onnx
m = onnx.load("/content/onnx_out/edsr_mini_48x12_static.onnx")
onnx.checker.check_model(m)
print("ONNX is valid and self-contained")


ONNX is valid and self-contained
